# TM10007 Assignment template -- ECG data

## Data loading and cleaning

Below are functions to load the dataset of your choice. After that, it is all up to you to create and evaluate a classification method. Beware, there may be missing values in these datasets. Good luck!

Importing modules

In [31]:
import os
import zipfile
import pandas as pd
import numpy as np 
import matplotlib.pyplot as plt
from sklearn import datasets as ds
import seaborn
import math
import statistics
import math
import matplotlib.pyplot as plt
from sklearn import datasets as ds
import seaborn

import numpy as np
from scipy.stats import shapiro 
from scipy.stats import lognorm
from scipy.spatial.distance import cdist


# Classifiers
from sklearn import model_selection
from sklearn import metrics
from sklearn import feature_selection 
from sklearn import preprocessing
from sklearn import neighbors
from sklearn import svm
from sklearn.feature_selection import SelectKBest
from sklearn.feature_selection import f_classif
from sklearn.svm import SVC
from sklearn.svm import svm
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier

cwd = os.getcwd() # This fn will return the Current Working Directory

zip_path = os.path.join(cwd, 'ecg', 'ecg_data.zip')
with zipfile.ZipFile(zip_path, 'r') as zip_ref:
    zip_ref.extractall(os.path.join(cwd, 'ecg'))

data_path = os.path.join(cwd, 'ecg', 'ecg_data.csv')
data = pd.read_csv(data_path, index_col=0)

ImportError: cannot import name 'svm' from 'sklearn.svm' (c:\Users\Julia Binder\miniconda3\lib\site-packages\sklearn\svm\__init__.py)

Exploring data part 1
- How many people have a normal ECG?
- How many people have an abnormal ECG?

In [14]:
# split labels from data
x = data.loc[:, data.columns != 'label']  #alles behalve label
y = data['label']  # labels

# normal / abnormal ECGs
total_abnormal_ECG = np.count_nonzero(y)  # current dataset has 146 nonzeros
total_normal_ECG = y.size -np.count_nonzero(y)  # current dataset has 681 zeros
percentage_abnormal = total_abnormal_ECG / (total_abnormal_ECG + total_normal_ECG)*100  # 17.65 %

Splitting data into training and test data
- Subset training and test based on ratios
- Stratification
- Cross-validation?




In [15]:
# Split data
X_train, X_test_DO_NOT_FIT, y_train, y_test_DO_NOT_FIT = model_selection.train_test_split(x, y, test_size=0.25, stratify=y)
y_train_ab = y_train==1  # waarom maken we hier bools van? ipv 1 en 0 hebben we nu true en false
# X_test_DO_NOT_FIT and y_test_DO_NOT_FIT SHOULD NOT BE USED FOR FITTING!!

# Scale the data to be normal
scaler = preprocessing.RobustScaler()
scaler.fit(X_train)
X_train = scaler.transform(X_train)
X_test_scaled_DO_NOT_FIT = scaler.transform(X_test_DO_NOT_FIT)

X_train=pd.DataFrame(X_train)
X_test_scaled_DO_NOT_FIT = pd.DataFrame(X_test_scaled_DO_NOT_FIT)

# Cross-validation
# cv_20fold = model_selection.StratifiedKFold(n_splits=10) --> uit college 1.2_generalization.ipyb

# Loop over the folds
#for validation_index, test_index in cv_20fold.split(X2, y2):
    # Split the data properly
#    X_validation = X2[validation_index]
#    y_validation = y2[validation_index]
    
#    X_test = X2[test_index]
#    y_test = y2[test_index]


Missing data
- Removing features if there is lot of data missing (replace all for a value)
- Removing samples (in this case patients) if there is a lot of data missing
- Imputation for generating data to fill us missing values -> median

In [16]:
# Missing data
X_train = X_train.replace(0, np.nan)  # make all zeros to NaN
nan_count = X_train.isna().sum().sum()  # count missing data -> 10500 in our dataset

# Delete missing data when > --% of feature of sample is missing
X_train = X_train.dropna(axis='columns', how='all') # deletes a feature if all values of a column (so feature) are empty
X_train = X_train.dropna(axis='rows', how='all') # deletes a patient if all values of a row (so sample) are empty

# Missing data to median per feature
for column in X_train.columns:
    X_train[column].fillna(X_train[column].median(), inplace=True)

Exploring data part 2
- Is the data normally distributed?

In [17]:
# Normally distributed
stat = []
p = []
for col in X_train.columns:
    if X_train[col].dtype == 'float64' or X_train[col].dtype == 'int64':
        s, pv = shapiro(X_train[col])
        stat.append(s)
        p.append(pv)
    else:
        stat.append(None)
        p.append(None)

Outliers
- Detect outliers using Z-score since data is not nornally distributed
- Replace outliers by the median of that feature
- Print -> check wether the outliers are changed 

In [18]:
# create a new dataframe to store the results
results = pd.DataFrame({'Column': X_train.columns, 'W': stat, 'p-value': p}) 
mean_p_value = results['p-value'].mean()  # p-value is really small. If p-value is bigger than 0.05, then data is normally distributed. SO its not
median_p_value = results['p-value'].median()  # p-value is really small. If p-value is bigger than 0.05, then data is normally distributed. SO its not

# Outliers: Tukey's fence 
k=3
fences=pd.DataFrame()
outliers = pd.DataFrame(False, index=X_train.index, columns=X_train.columns) # create an empty DataFrame for outliers

for col in X_train.columns:
    q1, q3 = np.percentile(X_train[col], [25, 75])
    iqr = q3 - q1
    lower_fence = q1 - k*iqr
    upper_fence = q3 + k*iqr
    fences[col]=[lower_fence, upper_fence]
    for row in X_train.index:
        if X_train.loc[row, col] < lower_fence or X_train.loc[row, col] > upper_fence:
            outliers.loc[row, col] = True # mark the place as an outlier

row_count = (outliers == True).sum(axis=1)
col_count = (outliers == True).sum(axis=0)
total_count = row_count.sum() + col_count.sum()
print(f'The total outliers in dataset x is {total_count}')

C:\Users\Julia Binder\AppData\Local\Temp\ipykernel_12596\3304028950.py:16: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  fences[col]=[lower_fence, upper_fence]
C:\Users\Julia Binder\AppData\Local\Temp\ipykernel_12596\3304028950.py:16: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  fences[col]=[lower_fence, upper_fence]
C:\Users\Julia Binder\AppData\Local\Temp\ipykernel_12596\3304028950.py:16: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor perfor

The total outliers in dataset x is 345560


C:\Users\Julia Binder\AppData\Local\Temp\ipykernel_12596\3304028950.py:16: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  fences[col]=[lower_fence, upper_fence]
C:\Users\Julia Binder\AppData\Local\Temp\ipykernel_12596\3304028950.py:16: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  fences[col]=[lower_fence, upper_fence]
C:\Users\Julia Binder\AppData\Local\Temp\ipykernel_12596\3304028950.py:16: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor perfor

In [19]:
# create a copy of x to modify
new_x = X_train.copy()

# replace outliers with median of x by column
for col in outliers.columns:
    median = X_train.loc[outliers[col] == False, col].median() # median of column where outlier is False
    new_x.loc[outliers[col], col] = median # replace outliers with median


In [20]:
# Check wether there are still outliers or not
k=3
fences=pd.DataFrame()
outliers = pd.DataFrame(False, index=X_train.index, columns=X_train.columns) # create an empty DataFrame for outliers

for col in new_x.columns:
    q1, q3 = np.percentile(X_train[col], [25, 75])
    iqr = q3 - q1
    lower_fence = q1 - k*iqr
    upper_fence = q3 + k*iqr
    fences[col]=[lower_fence, upper_fence]
    for row in new_x.index:
        if new_x.loc[row, col] < lower_fence or new_x.loc[row, col] > upper_fence:
            outliers.loc[row, col] = True # mark the place as an outlier

row_count = (outliers == True).sum(axis=1)
col_count = (outliers == True).sum(axis=0)
total_count = row_count.sum() + col_count.sum()

print(f'total outliers of the filtered x is {total_count}')


C:\Users\Julia Binder\AppData\Local\Temp\ipykernel_12596\3614173827.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  fences[col]=[lower_fence, upper_fence]
C:\Users\Julia Binder\AppData\Local\Temp\ipykernel_12596\3614173827.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  fences[col]=[lower_fence, upper_fence]
C:\Users\Julia Binder\AppData\Local\Temp\ipykernel_12596\3614173827.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor perfor

total outliers of the filtered x is 0


C:\Users\Julia Binder\AppData\Local\Temp\ipykernel_12596\3614173827.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  fences[col]=[lower_fence, upper_fence]
C:\Users\Julia Binder\AppData\Local\Temp\ipykernel_12596\3614173827.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead. To get a de-fragmented frame, use `newframe = frame.copy()`
  fences[col]=[lower_fence, upper_fence]
C:\Users\Julia Binder\AppData\Local\Temp\ipykernel_12596\3614173827.py:11: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor perfor

In [21]:
#change the x_train to the new_x
X_train = new_x

Feature selection: lets try -> LET OP: VOOR NU EVEN ALLE DATA, DIT NOG AANPASSEN
- Greedy
- Univariate

In [22]:
# Greedy method


# Univariate method
x_univar = SelectKBest(f_classif, k=10).fit_transform(x, y)  # welke k wil je? 
print(x_univar.shape)

(827, 10)


K-Neirest Neighbour classifier

In [26]:
k_list = [1, 3, 7]
from sklearn import neighbors

for k in k_list:
    clf_knn = neighbors.KNeighborsClassifier(n_neighbors=k)
    clf_knn.fit(X_train, y_train)

    # Test the classifier on the training data and plot
    score_train = clf_knn.score(X_train, y_train)

    # Test the classifier on the test data and plot
    score_test = clf_knn.score(X_test_scaled_DO_NOT_FIT,y_test_DO_NOT_FIT)

print(f'test score os {score_test}')
print(score_train)

0.8309178743961353
0.832258064516129


*Support Vector Machines* 
Altough Support Vector Machines are quite intuitive and easy to use, they have quite a lot of hyperparameters. One general and highly important parameter is the slack C, which defaults to 1.0 in scikit learn. The SVM in scikit-learn contains defaults for the linear, polynomial and radial basis function kernels, and has options for their specific hyperparameters. However, SVMs also accept manually constructed and precomputed kernels.

*KNeighbours Classifiers*
*Random forest*
*Kernels*

In [35]:
# Construct classifiers
from sklearn.neighbors import KNeighborsClassifier
from sklearn.ensemble import RandomForestClassifier

svmlin = SVC(kernel='linear', gamma='scale')
svmrbf = SVC(kernel='rbf', gamma='scale')
svmpoly = SVC(kernel='poly', degree=3, gamma='scale')

clsfs = [KNeighborsClassifier(), RandomForestClassifier(), svmlin, svmpoly, svmrbf]



for clf in clsfs:
    clf.fit(X_train, y_train)
    y_pred = clf.predict(x)
    print(f'Misclassified: %d / %d % {((y != y_pred).sum(), x.shape[0])}' )

c:\Users\Julia Binder\miniconda3\lib\site-packages\sklearn\base.py:402: UserWarning: X has feature names, but KNeighborsClassifier was fitted without feature names
  warnings.warn(


Misclassified: %d / %d % (151, 827)


c:\Users\Julia Binder\miniconda3\lib\site-packages\sklearn\base.py:402: UserWarning: X has feature names, but RandomForestClassifier was fitted without feature names
  warnings.warn(


Misclassified: %d / %d % (680, 827)


c:\Users\Julia Binder\miniconda3\lib\site-packages\sklearn\base.py:402: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(


Misclassified: %d / %d % (238, 827)


c:\Users\Julia Binder\miniconda3\lib\site-packages\sklearn\base.py:402: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(


Misclassified: %d / %d % (364, 827)


c:\Users\Julia Binder\miniconda3\lib\site-packages\sklearn\base.py:402: UserWarning: X has feature names, but SVC was fitted without feature names
  warnings.warn(


Misclassified: %d / %d % (146, 827)
